In [1]:
%run /home/bb/src/python/valkyrie/lib/valkyrie/apps/common/run_notebook_import.py

/media/veracrypt1/python/valkyrie/lib/valkyrie/apps/common/run_notebook_import.py:16: DeprecationWarning: Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython display
  from IPython.core.display import display, HTML


/media/veracrypt1/python/valkyrie/lib/valkyrie/ml/data.py:291: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @jit


In [2]:
sdate, edate = '2023-01-01', '2023-06-30'
instrs = ['BDM.BTC.USDT.FP']
freq = '1s'
ret_n_s = [60, 120, 300, 600]
root_dir = '/home/bb/data/BDM'
#########################################################
#DataMgr
#########################################################
data_mgr = DataMgr(sdate, edate, freq, root_dir, instrs = instrs, ret_n_s = ret_n_s)
df_res = data_mgr.get(instrs[0])
channels = ['bpx_last','apx_last'] + ['bq_last','aq_last','buy_qty_sum', 'sell_qty_sum'] 
n_channels = len(channels)
H, W = 16, 64
df2t2 = Df2T2(df_res, H, W, xcols = channels, ycol = 'mid_last_ret_300_n', yscaler = 1)

train_set, val_set = TrainValDataSet.create_train_valiation_pair(df2t2, 0.8)
dm = DataModule.from_dataset(train_set, val_set, 2048)

after dropping na 15637615 -> 15604848


# LR Net

In [ ]:
from valkyrie.ml.net import LrNet
lr_net = LrNet(lr = 0.001)

In [ ]:

X = df2t2[0][0]
ml_utils.layer_summary(lr_net, X.shape)
#ml_utils.parameter_summary(testNet)

In [ ]:
trainer = ml_modules.Trainer(max_epochs=100, log_fn = 'alex_net_300s_mul2.log')
with Timer('training'):
    trainer.fit(lr_net, dm)

In [ ]:
ne = NetEvaluator(lr_net, dm)
ne.eval_performance()

# Anet

In [3]:
alex_reg_net1 = AlexRegNet(lr = 1e-3, num_channels = n_channels, height = H, down_mul = 1)
X = df2t2[0][0]
ml_utils.layer_summary(alex_reg_net1, X.shape)
#ml_utils.parameter_summary(testNet)

input shape torch.Size([6, 16, 64])
name : BatchNormAlongW output shape:	 torch.Size([1, 6, 16, 64])
name : Conv2d output shape:	 torch.Size([1, 96, 16, 64])
name : LeakyReLU output shape:	 torch.Size([1, 96, 16, 64])
name : MaxPool2d output shape:	 torch.Size([1, 96, 7, 31])
name : Conv2d output shape:	 torch.Size([1, 384, 7, 31])
name : LeakyReLU output shape:	 torch.Size([1, 384, 7, 31])
name : Conv2d output shape:	 torch.Size([1, 256, 7, 31])
name : LeakyReLU output shape:	 torch.Size([1, 256, 7, 31])
name : MaxPool2d output shape:	 torch.Size([1, 256, 3, 15])
name : Flatten output shape:	 torch.Size([1, 11520])
name : Linear output shape:	 torch.Size([1, 4096])
name : LeakyReLU output shape:	 torch.Size([1, 4096])
name : Dropout output shape:	 torch.Size([1, 4096])
name : Linear output shape:	 torch.Size([1, 1])


/home/bb/anaconda3/lib/python3.11/site-packages/torch/nn/modules/lazy.py:180: UserWarning: Lazy modules are a new feature under heavy development so changes to the API or functionality can happen at any moment.
  warnings.warn('Lazy modules are a new feature under heavy development '


In [4]:
trainer = ml_modules.Trainer(max_epochs=400, log_fn = 'alex_300s_e400.log')
with Timer('training'):
    trainer.fit(alex_reg_net1, dm)

training finished in : 273944.727179 secs


In [5]:
ne = NetEvaluator(alex_reg_net1, dm)
ne.eval_performance()

(tensor(0.8653, device='cuda:0'),
 tensor(0.0001, device='cuda:0'),
 tensor(0.0009, device='cuda:0'))

# Channel = 6

In [ ]:
alex_reg_net2 = AlexRegNet(lr = 1e-4, num_channels = n_channels, height = H, down_mul = 1)
X = df2t2[0][0]
ml_utils.layer_summary(alex_reg_net2, X.shape)
#ml_utils.parameter_summary(testNet)

In [ ]:
trainer = ml_modules.Trainer(max_epochs=100, log_fn = 'alex_300s_m2.log')
with Timer('training'):
    trainer.fit(alex_reg_net1, dm)

In [ ]:
ne = NetEvaluator(alex_reg_net1, dm)
ne.eval_performance()

In [ ]:
print(2)

In [ ]:
torch.backends.cudnn.allow_tf32 = True
torch.backends.cuda.matmul.allow_tf32 = True

In [ ]:
alex_reg_net2B = AlexRegNet(lr = 1e-4, num_channels = n_channels, height = H, down_mul = 1)
X = df2t2[0][0]
ml_utils.layer_summary(alex_reg_net2B, X.shape)
#ml_utils.parameter_summary(testNet)

In [ ]:
trainer = ml_modules.Trainer(max_epochs=100, log_fn = 'alex_300s_m2B.log')
with Timer('training'):
    trainer.fit(alex_reg_net2B, dm)